In [1]:
import pandas as pd
import numpy as np
from scipy.stats import zscore
import statsmodels.api as sm
import random

In [49]:
# Read data from the Excel file
input_file = 'Returns_short_interest_data2021.xlsx'
input_file1= 'SII_through_2021.xlsx'
input_sheet = 'GW variables'
input_sheet1= 'Returns'

# Load data from 'GW variables' sheet
gw_variables = pd.read_excel(input_file, sheet_name=input_sheet, usecols="K,Q", skiprows=1224, nrows=588, header=None)
gw_variables1 = pd.read_excel(input_file, sheet_name=input_sheet, usecols="K,Q", skiprows=1225, nrows=588, header=None)

Rfree_lag = gw_variables.iloc[:, 0]
R_VW_SP500 = gw_variables1.iloc[:, 1]

# Load data from 'Returns' sheet
#returns = pd.read_excel(input_file, sheet_name=input_sheet1 , usecols= "C, D, E", skiprows=1, nrows=504, header=None)
#R_EW_SP500 = returns.iloc[:,0]
#R_VW_CRSP = returns.iloc[:,1]
#R_EW_CRSP = returns.iloc[:,2]

# Calculate the equity risk premium for each investment strategy
r_VW_SP500 = np.log(1 + R_VW_SP500) - np.log(1 + Rfree_lag)
#r_EW_SP500 = np.log(1 + R_EW_SP500) - np.log(1 + Rfree_lag)
#r_VW_CRSP = np.log(1 + R_VW_CRSP) - np.log(1 + Rfree_lag)
#r_EW_CRSP = np.log(1 + R_EW_CRSP) - np.log(1 + Rfree_lag)

# Combine the equity risk premium data for all investment strategies into a single matrix
r = np.column_stack((r_VW_SP500))
r = r.T

/Users/jorgenlunner/opt/anaconda3/lib/python3.9/site-packages/openpyxl/worksheet/header_footer.py:48: UserWarning: Cannot parse header or footer so it will be ignored
  warn("""Cannot parse header or footer so it will be ignored""")
/Users/jorgenlunner/opt/anaconda3/lib/python3.9/site-packages/openpyxl/worksheet/_reader.py:312: UserWarning: Unknown extension is not supported and will be removed
  warn(msg)
/Users/jorgenlunner/opt/anaconda3/lib/python3.9/site-packages/openpyxl/worksheet/header_footer.py:48: UserWarning: Cannot parse header or footer so it will be ignored
  warn("""Cannot parse header or footer so it will be ignored""")
/Users/jorgenlunner/opt/anaconda3/lib/python3.9/site-packages/openpyxl/worksheet/_reader.py:312: UserWarning: Unknown extension is not supported and will be removed
  warn(msg)


In [50]:
# Load Goyal-Welch predictor data, 1973:01-2021:12
GW = np.load('Program_generate_GW2_predictors.npy')
GW_standardize = zscore(GW, ddof=1)

In [51]:
# Load data from 'Short interest' sheet
short_interest = pd.read_excel(input_file1, sheet_name='Sheet1', usecols= "C", skiprows=1, nrows=590, header=None)
SII_EWSI = short_interest.to_numpy()

In [52]:
# Compute cumulative returns

h = [1, 3, 6, 12]


num_rows, num_columns = r.shape

r_h = np.empty((num_rows, len(h), num_columns))
r_h[:] = np.nan

for j in range(len(h)):
    for k in range(num_columns):
        for t in range(num_rows - (h[j] - 1)):
            r_h[t, j, k] = np.mean(r[t:t + h[j], k])


In [53]:
#r_h= r_h.T
r_h.shape

(588, 4, 1)

In [54]:
# Define subsamples observations

indicator_sub = np.zeros((len(r), 10))

index_sub_1 = np.arange(0, (1982 - 1972) * 12)  # 1973:01-1982:12
indicator_sub[index_sub_1, 0] = 1

index_sub_2 = np.arange((1982 - 1972) * 12, (1992 - 1972) * 12)  # 1983:01-1992:12
indicator_sub[index_sub_2, 1] = 1

index_sub_3 = np.arange((1992 - 1972) * 12, (2002 - 1972) * 12)  # 1993:01-2002:12
indicator_sub[index_sub_3, 2] = 1

index_sub_4 = np.arange((2002 - 1972) * 12, (2014 - 1972) * 12)  # 2003:01-2014:12
indicator_sub[index_sub_4, 3] = 1

index_sub_5 = np.arange((2007 - 1972) * 12, (2014 - 1972) * 12)  # 2008:01-2014:12
indicator_sub[index_sub_5, 4] = 1

index_sub_6 = np.arange((2008 - 1972) * 12, (2014 - 1972) * 12)  # 2009:01-2014:12
indicator_sub[index_sub_6, 5] = 1

index_sub_7 = np.arange((1982 - 1972) * 12, (2007 - 1972) * 12)  # 1973:01-2007:12
indicator_sub[index_sub_7, 6] = 1

index_sub_8 = np.arange((2007 - 1972) * 12, (2021 - 1972) * 12)  # 2008:01_2021:12
indicator_sub[index_sub_8, 7] = 1

index_sub_9 = np.arange((2008 - 1972) * 12, (2021 - 1972) * 12)  # 2009:01_2021:12
indicator_sub[index_sub_9, 8] = 1

index_sub_10 = np.arange((1982 - 1972) * 12, (2021 - 1972) * 12)  # 1973:01_2021:12
indicator_sub[index_sub_10, 9] = 1

In [55]:
beta_hat_subsample = np.empty((indicator_sub.shape[1], 4, len(h)))

for j in range(len(h)):
    
    # Subsample analysis 
    for i in range(indicator_sub.shape[1]): 
        index_sub_i = np.where(indicator_sub[:, i] == 1)[0]
        X_i_j = np.column_stack((np.ones(len(index_sub_i)), -SII_EWSI[index_sub_i, 0]))
        y_i_j = r_h[index_sub_i, j, 0]
        if j== 0: 
            results_i_j = sm.OLS(100 * y_i_j[1:], X_i_j[:-h[j], :]).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
        else:
            results_i_j = sm.OLS(100 * y_i_j[1:-h[j]+1], X_i_j[:-h[j], :]).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
        beta_hat_subsample[i, :, j] = [results_i_j.params[1], results_i_j.tvalues[1], np.nan, 100 * results_i_j.rsquared]

In [56]:
# Compute fixed-regressor wild bootstrap p-values
X_sink = np.column_stack((GW_standardize, SII_EWSI[:, 0]))
X_sink = np.delete(X_sink, [3, 10], axis=1)
X_sink = np.column_stack((np.ones(len(r)), SII_EWSI))
epsilon_hat = np.empty((len(r_h) - 1, r.shape[1]), dtype=np.float64)
epsilon_hat[:] = np.nan

for k in range(r.shape[1]):
    results_k = sm.OLS(r[1:, k], X_sink[:-1, :]).fit()
    epsilon_hat[:, k] = results_k.resid

In [57]:
B = 1000
beta_hat_tstat_subsample_star = np.empty((B, indicator_sub.shape[1], len(h)), dtype=np.float64)
beta_hat_tstat_subsample_star[:] = np.nan

In [58]:
random.seed(0)  # for reproducibility

for b in range(B):
    u_star_b = np.random.randn(len(r) - 1)
    r_star_b = np.empty((len(r), r.shape[1]), dtype=np.float64)
    r_star_b[:] = np.nan
    
    for k in range(r.shape[1]):
        r_star_b[:, k] = np.concatenate(([r[0, k]], r[:, k].mean() + epsilon_hat[:, k] * u_star_b))
    
    r_h_star_b = np.empty((len(r_h), len(h), r.shape[1]), dtype=np.float64)
    r_h_star_b[:] = np.nan
    for j in range(len(h)):
        for k in range(r.shape[1]):
            for t in range(len(r_h) - (h[j] - 1)):
                r_h_star_b[t, j, k] = r_star_b[t:t + h[j], k].mean()
    for j in range(len(h)):
        for i in range(indicator_sub.shape[1]):
            index_sub_i = np.where(indicator_sub[:, i] == 1)[0]
            X_i_j = np.column_stack((np.ones(len(index_sub_i)), -SII_EWSI[index_sub_i, 0]))
            y_i_j_star_b = r_h_star_b[index_sub_i, j, 0]
            if j == 0:
                results_i_j_star_b = sm.OLS(100*y_i_j_star_b[1:], X_i_j[:-h[j], :]).fit(cov_type='HAC',cov_kwds={'maxlags':h[j]})
            else: 
                results_i_j_star_b = sm.OLS(100*y_i_j_star_b[1:-h[j] + 1], X_i_j[:-h[j], :]).fit(cov_type='HAC',cov_kwds={'maxlags':h[j]})
            beta_hat_tstat_subsample_star[b, i, j] = results_i_j_star_b.tvalues[1]

In [59]:
for j in range(len(h)):
    for i in range(indicator_sub.shape[1]):
        beta_hat_subsample[i, 2, j] = np.sum(beta_hat_tstat_subsample_star[:, i, j] > beta_hat_subsample[i, 1, j]) / B

In [60]:
beta_hat_subsample[:,:,0]

array([[ 1.13810153e+00,  2.03449513e+00,  2.20000000e-02,
         1.69182643e+00],
       [ 9.37799729e-01,  1.09185951e+00,  1.48000000e-01,
         9.77260962e-01],
       [ 1.01267320e+00,  9.83104589e-01,  1.81000000e-01,
         7.74898993e-01],
       [ 1.17953192e+00,  2.48057495e+00,  1.00000000e-03,
         5.40369021e+00],
       [ 1.75223870e+00,  2.03254717e+00,  3.00000000e-02,
         8.60151173e+00],
       [-2.69950360e-01, -2.57559018e-01,  5.94000000e-01,
         1.01050690e-01],
       [ 3.00440761e-01,  1.07356028e+00,  1.56000000e-01,
         2.12531065e-01],
       [ 6.48315423e-01,  1.68861855e+00,  6.50000000e-02,
         3.18286487e+00],
       [ 4.00743009e-02,  1.12990733e-01,  4.88000000e-01,
         1.03360111e-02],
       [ 5.20789387e-01,  2.39527222e+00,  6.00000000e-03,
         1.46898168e+00]])

In [22]:
# Write results to excel file 
output_file = 'Returns_short_interest_results.xlsx'
output_sheet = 'SII to 2021'

with pd.ExcelWriter(output_file, engine='openpyxl', mode='a',if_sheet_exists='overlay') as writer:
    pd.DataFrame(beta_hat_subsample[:,:,0]).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=3, header=False, index=False)
    pd.DataFrame(beta_hat_subsample[:,:,1]).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=8, header=False, index=False)
    pd.DataFrame(beta_hat_subsample[:,:,2]).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=13, header=False, index=False)
    pd.DataFrame(beta_hat_subsample[:,:,3]).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=18, header=False, index=False)
    pd.DataFrame(SII_EWSI).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=24, header=False, index=False)
   